ЗАДАНИЕ 1.

In [25]:
!pip install nglview --user

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


Импорт модулей:

In [26]:
import nglview as nv
import requests         
import json  

Создаем заготовку запроса:

In [27]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

In [28]:
#Ключевое слово
keyword_clause = {
    "type": "terminal",
    "service": "full_text", 
    "parameters": {
        "value": "androgen"
    }
}

my_query["query"]["nodes"].append(keyword_clause)

In [29]:
#Разрешение
resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.0,
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [30]:
#Число лигандов 
has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0,
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [31]:
#Дата
date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2005-01-01", 
            "to": "2010-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [32]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query) 

search = requests.post(f'{rcsb}', data=json_query)

In [33]:
search_result = search.json() 
search_result

{'query_id': '14cd5027-7df1-4bef-af36-b3a3b9592fab',
 'result_type': 'entry',
 'total_count': 99,
 'result_set': [{'identifier': '2AX6',
   'score': 1.0,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 12534, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 12004, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 19354, 'original_score': 1.0, 'norm_score': 1.0}]},
    {'service_type': 'full_text',
     'nodes': [{'node_id': 14918,
       'original_score': 9.654606819152832,
       'norm_score': 1.0}]}]},
  {'identifier': '2PIT',
   'score': 1.0,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 12534, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 12004, 'original_score': 1.0, 'norm_score': 1.0},
      {'node_id': 19354, 'original_score': 1.0, 'norm_score': 1.0}]},
    {'service_type': 'full_text',
     'nodes': [{'node_id': 14918,
       'original_score': 9.654606819152832,
       'norm_score': 1.0}]}]},
  {'id

In [34]:
#Находим лучший результат
best_hit = search_result["result_set"][0] 
best_hit

{'identifier': '2AX6',
 'score': 1.0,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 12534, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 12004, 'original_score': 1.0, 'norm_score': 1.0},
    {'node_id': 19354, 'original_score': 1.0, 'norm_score': 1.0}]},
  {'service_type': 'full_text',
   'nodes': [{'node_id': 14918,
     'original_score': 9.654606819152832,
     'norm_score': 1.0}]}]}

Я далее буду работать с PDB ID 2AX6.

ЗАДАНИЕ 2.

Я нашла запись о кристаллической структуре мутанта T877A домена связывания лиганда рецептора андрогена в комплексе с гидроксифлутамидом. Мутанты T877A - это селективные модуляторы рецепторов андрогенов, которые по структуре напоминают нестероидные антагонисты, но действуют как агонисты рецепторов андрогенов тканеселективным образом.

ЗАДАНИЕ 3.

In [35]:
#Структура белка
view = nv.show_pdbid('2ax6') 
view

NGLWidget()

In [36]:
from ipywidgets import interact, fixed

In [39]:
#Типы отображений
representations = [
  'ball+stick',      # шаростержневая модель
  'backbone',        # прямые линии, соединяющие С-альфа атомы
  'cartoon',         # условное отображение вторичной структуры
  'helixorient',     # упрощенное отображение 
  'hyperball',       # сглаженная шаростержневая модель
  'licorice',        # стержневая модель (без шаров)
  'line',            # очень тонкая стержневая модель
  'point',           # атомы в виде плоских точек
  'ribbon',          # отображение остова в виде ленты
  'rocket',          # отображение альфа-спиралей как цилиндров
  'rope',            # отображение остова в виде колбасы
  'spacefill',       # атомы в виде шаров соотв. Ван-дер-Ваальсова радиуса
  'surface',         # поверхность
  'trace',           # сглаженная линия, соединяющая С-альфа атомы
  'tube'             # более сдержанный rope
]

In [40]:
#Типы окрашивания
colors = [
  'random',
  'uniform',
  'atomindex',      # от синего к красному с ростом номера атома
  'residueindex',   # от синего к красному с ростом номера остатка
  'chainindex',     # каждой цепи свой цвет
  'sstruc',         # стандартные цвета для типа вторичной структуры
  'element',        # стандартные цвета для химических элементов
  'resname',        # свой цвет каждому из 20 остатков
  'bfactor',        # чем темнее, тем подвижнее
  'hydrophobicity', # чем темнее, тем гидрофобнее
]

In [42]:
my_examples = {
    'Отображение 1': {
        'description': '''
Вариант 2.
Белок в виде cartoon, покраска от N к C концу
Боковые радикалы покрашены в светло-серый, показаны линиями
Боковые радикалы заряженных аминокислот показаны в стержневой модели
Лиганды показаны в шаростержневой модели, покрашены по элементам, углерод покрашен в любой цвет, кроме стандартного
''',
        'representations' : [
    {
        'type': 'cartoon',                      
        'params': {
            'sele': 'protein',               
            'color': 'residueindex'  
          }
    },
    {
        'type': 'line',                      
        'params': {
            'sele': 'sidechainAttached',                     
            'color': 'lightgray'  
          }
    },
    {
        'type': 'licorice',                      
        'params': {
            'sele': 'sidechainAttached and charged',                     
            'color': 'element'  
          }
    },
    {
                'type': 'ball+stick',
                'params': {
                    'sele': 'ligand',                 
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand and _C',                
                    'color': 'yellow'  
                 }
            }
            
      ],
        
}, 'Отображение 2': {
        'description': '''
Вариант 4.
Белок в виде cartoon, покраска по типу вторичной структуры
Боковые радикалы покрашены по элементу, показаны линиями
Боковые радикалы ароматических аминокислот показаны в стержневой модели
Лиганды показаны в виде Ван-дер-Ваальсовых сфер, покрашены по гидрофобности.
''',
     'representations' : [
         {
        'type': 'cartoon',                      
        'params': {
            'sele': 'protein',               
            'color': 'sstruc'  
          }
    },
    {
        'type': 'line',                      
        'params': {
            'sele': 'sidechainAttached',                     
            'color': 'element'  
          }
    },
    {
        'type': 'licorice',                      
        'params': {
            'sele': 'sidechainAttached and aromatic',                     
            'color': 'element'  
          }
    },
    {
                'type': 'spacefill',
                'params': {
                    'sele': 'ligand',                 
                    'color': 'hydrophobicity'  
                 }
     }
  ],
    }, 'Отображение 3': {
        'description': '''
Вариант 10.
Белок в виде cartoon белого цвета
Cartoon для остатков с 20-го по 55-й покрашен в зеленый
Для остатков с 20-го по 55-й показаны боковые радикалы в модели hyperball, покраска по элементам
Лиганды показаны в шаростержневой модели, покраска по элементам
''', 
    'representations' : [
        {
        'type': 'cartoon',                      
        'params': {
            'sele': 'protein',               
            'color': 'white'  
          }
    },
    {
        'type': 'cartoon',                      
        'params': {
            'sele': 'protein and 20-55',                     
            'color': 'green'  
          }
    },
    {
        'type': 'hyperball',                      
        'params': {
            'sele': 'sidechainAttached and 20-55',                     
            'color': 'element'  
          }
    },
    {
                'type': 'ball+stick',
                'params': {
                    'sele': 'ligand',                 
                    'color': 'element'  
                 }
      }
    ],
    },
}

Создаем интерактивную ячейку

In [43]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("2ax6", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Отображение 1', 'Отображение 2', 'Отображ…

NGLWidget()